# Prep

Setting up some prior functionality

In [1]:
import shutil

original="../input/motivepredata/MotiveChallenge"
target="/kaggle/working/MotiveChallenge/"
shutil.copytree(original,target)


'/kaggle/working/MotiveChallenge/'

In [2]:
#../input/k/khizerali/urpc-2019-underwater-detro/MotiveChallenge/data/train2017/00077ee2-cf2f-46af-a832-6c74681c37be.jpeg
original="../input/k/khizerali/urpc-2019-underwater-detro/MotiveChallenge/detr-master/outputs/"
target="/kaggle/working/MotiveChallenge/20_epoch_weights/"
shutil.copytree(original,target)


'/kaggle/working/MotiveChallenge/20_epoch_weights/'

In [3]:
#../input/k/khizerali/urpc-2019-underwater-detro/MotiveChallenge/data/train2017/00038202-0360-49eb-a44a-e02047a404ea.jpeg

In [4]:
cd '/kaggle/working/MotiveChallenge/detr-master/'

/kaggle/working/MotiveChallenge/detr-master


In [5]:
!pip install pycocotools
!pip install torch==1.8.0 torchvision==0.9.0 -qq
!pip install --upgrade --no-cache-dir gdown

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 106.6/106.6 KB 564.4 kB/s eta 0:00:00
  Installing build dependencies ... - \ | / - \ | / - \ | done
  Getting requirements to build wheel ... - \ done
  Preparing metadata (pyproject.toml) ... - done
  Created wheel for pycocotools: filename=pycocotools-2.0.4-cp37-cp37m-linux_x86_64.whl size=370009 sha256=3e54a2033913a631cd12df08836a86f52c652b4a1f14ab4237afefa765ac3cb3
  Stored in directory: /root/.cache/pip/wheels/a3/5f/fa/f011e578cc76e1fc5be8dce30b3eb9fd00f337e744b3bba59b
Successfully built pycocotools
  Installing build dependencies ... - \ | done
  Getting requirements to build wheel ... - done
  Preparing metadata (pyproject.toml) ... - done
  Created wheel for gdown: filename=gdown-4.5.1-py3-none-any.whl size=14933 sha256=d6e402ed5410609c3a3bd3067b9e455e6e21a1974024b71bc1d1f8c48408d3c4
  Stored in directory: /tmp/pip-ephem-wheel-cache-10d8p5md/wheels/3d/ec/b0/a96d1d126183f98570a785e6bf8789fca559853a

In [6]:
#https://drive.google.com/file/d/1YsMqgcVKBO11oHRWkR86eJuyjCX4hGMg/view?usp=sharing
!gdown --id 1YsMqgcVKBO11oHRWkR86eJuyjCX4hGMg

/opt/conda/lib/python3.7/site-packages/gdown/cli.py:131: FutureWarning: Option `--id` was deprecated in version 4.3.1 and will be removed in 5.0. You don't need to pass it anymore to use a file ID.
  category=FutureWarning,
Downloading...
From: https://drive.google.com/uc?id=1YsMqgcVKBO11oHRWkR86eJuyjCX4hGMg
To: /kaggle/working/MotiveChallenge/detr-master/private_test_set_1.zip
100%|███████████████████████████████████████| 1.22G/1.22G [00:05<00:00, 204MB/s]


In [7]:
#import os 
#os.listdir(r'/kaggle/working/MotiveChallenge/detr-master/new_data/test_set_1/images')

In [8]:
import zipfile
path_to_zip_file='/kaggle/working/MotiveChallenge/detr-master/private_test_set_1.zip'
directory_to_extract_to='/kaggle/working/MotiveChallenge/detr-master/new_data'
with zipfile.ZipFile(path_to_zip_file, 'r') as zip_ref:
    zip_ref.extractall(directory_to_extract_to)

In [9]:
import torch, torchvision
print(torch.__version__, torch.cuda.is_available())

1.8.0 True


# Load a model

First we have to decide if our model should be pretrained. 

This greatly depends on the size of a dataset. Smaller datasets rely more on finetuning. 

# Dataset

Our dataset should be loadable as a COCO format

This allows us to use the pycocotools to load the data dict for the main python script

# Training

We use the main.py script to run our training

# Inference



In [10]:
import pandas as pd 
import os
from pycocotools.coco import COCO
import skimage.io as io
import matplotlib.pyplot as plt
from pathlib import Path
import torch, torchvision
import matplotlib.pyplot as plt
from PIL import Image


num_classes = 5
#imf = Image.open(r"D:\Motive AI Challenge\NoError_TrainingsRound\test2_images\0022b971-8948-4dc5-bb42-a6084287b50a.jpeg")


model = torch.hub.load('facebookresearch/detr',
                        'detr_resnet50',
                        pretrained=False,
                        num_classes=num_classes)



#model=torch.load(r'C:\Users\Administrator.DESKTOP-AD98P06\.cache\torch\hub\checkpoints\resnet34-b627a593.pth')
checkpoint = torch.load(r'/kaggle/working/MotiveChallenge/20_epoch_weights/checkpoint.pth',
                        map_location='cpu')

#del checkpoint["model"]["query_embed.weight"]


model.load_state_dict(checkpoint['model'],
                      strict=False)

model.eval();

import torchvision.transforms as T

# standard PyTorch mean-std input image normalization
transform = T.Compose([
    T.Resize(800),
    T.ToTensor(),
    T.Normalize([0.485, 0.456, 0.406], [0.229, 0.224, 0.225])
])





image_path=r"/kaggle/working/MotiveChallenge/detr-master/new_data/test_set_1/images"
from PIL import Image
import cv2
import glob
i=0
dict_1 = []
dict_2 = []

annotations=0

for img in glob.glob(r"/kaggle/working/MotiveChallenge/detr-master/new_data/test_set_1/images/*.jpg"):
    if i%20 == 0:
        f = open(r"/kaggle/working/Output_R2.txt", "a")
        f.write(str(dict_2))
        f.close()    
        dict_2=[]
        
    Keys = ["fle_name","id","height","width"]
    Values=[]
    Keys1=["image_id","bbox","category_id","id","confidence"]
    Values1=[]
    # cv_img = PIL.Image(img)
    
    print("file_name: ",str(os.path.basename(img)))
    # Values.append(str(os.path.basename(img)))
    # Values.append(int(i))
    # Values.append(int(cv_img.shape[0]))
    # Values.append(int(cv_img.shape[1]))
    # dct = dict(zip(Keys, Values))
    # dict_1.append(dct)
    
    #################################################
    # im= Image.fromarray(cv_img)
    im = Image.open(img)
    

    # for output bounding box post-processing
    def box_cxcywh_to_xyxy(x):
        x_c, y_c, w, h = x.unbind(1)
        b = [(x_c - 0.5 * w), (y_c - 0.5 * h),
             (x_c + 0.5 * w), (y_c + 0.5 * h)]
        return torch.stack(b, dim=1)

    def rescale_bboxes(out_bbox, size):
        img_w, img_h = size
        b = box_cxcywh_to_xyxy(out_bbox)
        b = b * torch.tensor([img_w, img_h, img_w, img_h], dtype=torch.float32)
        return b
    # Fine-tuned classes
    #Change the Required classes according to your use-case but they should be from the list of finetuned_classes.
    finetuned_classes = [ 'none' , 'Car', 'Truck', 'StopSign','traffic_lights' ]
    Required_classes = [  'Car', 'Truck', 'StopSign','traffic_lights']
    # colors for visualization
    COLORS = [[0.000, 0.447, 0.741], [0.850, 0.325, 0.098], [0.929, 0.694, 0.125],
              [0.494, 0.184, 0.556], [0.466, 0.674, 0.188], [0.301, 0.745, 0.933]]
    def return_cat_id(pil_img, prob=None, boxes=None):
        cat_ids = []


        colors = COLORS * 100
       # if prob is not None and boxes is not None:
        for p, (xmin, ymin, xmax, ymax), c in zip(prob, boxes.tolist(), colors):
            cl = p.argmax()
            
        #if finetuned_classes[cl] not in Required_classes:
        
            
            # print("Category Id: ",int(cl))
            cat_ids.append(int(cl))
            # print(len(cat_ids))
        return cat_ids
            


        #plt.show()
        
    def filter_bboxes_from_outputs(outputs,
                                   threshold):
      
      # keep only predictions with confidence above threshold
      probas = outputs['pred_logits'].softmax(-1)[0, :, :-1]
      keep = probas.max(-1).values > threshold

      probas_to_keep = probas[keep]
      
      
      # convert boxes from [0; 1] to image scales
      bboxes_scaled = rescale_bboxes(outputs['pred_boxes'][0, keep], im.size)
      img_ww, img_hh = im.size
      
      ck = outputs['pred_boxes'][0, keep]
      x_c, y_c, w, h = ck.unbind(1)
      b = [(x_c) , (y_c) ,(w) ,(h)]
      b=torch.stack(b, dim=1)
      bk = b*torch.tensor([img_ww, img_hh, img_ww, img_hh],dtype=torch.float32)
      bk=bk.to(torch.int32)
      return probas_to_keep, bboxes_scaled,bk

    def run_worflow(my_image, my_model):
      Keys1=["image_id","bbox","category_id","id","confidence"]
      Values1=[]
      global annotations
      global i
      # mean-std normalize the input image (batch-size: 1)
      img = transform(my_image).unsqueeze(0)
      #print(type(img))
      #print(img.shape)
      # propagate through the model
      outputs = my_model(img)
      
      
      out_logits, out_bbox = outputs['pred_logits'], outputs['pred_boxes']
      

      
      
    #you can change the threshold for object detection
      for threshold in [0.7]:
        
        probas_to_keep, bboxes_scaled,bk = filter_bboxes_from_outputs(outputs,
                                                                  threshold=threshold)
        # print(bboxes_scaled)
        # for i in range(0,len(probas_to_keep)):
        #     print("Confidence: ", float(probas_to_keep[i].max())) 
        cats = return_cat_id(im,probas_to_keep, 
        bboxes_scaled)
        
        # plot_finetuned_results(my_image,
        #                        probas_to_keep, 
        #                        bboxes_scaled)
        
        for J in range(0,len(probas_to_keep)):
            print("image id: ",i)
            print("annotation id:",annotations)
            Values1.append(int(i))
            Values1.append(bk[J])
            Values1.append(cats[J])
            Values1.append(int(annotations))
            annotations=annotations+1
            conf = float(probas_to_keep[J].max())
            conf = round(conf,2)
            #print(conf)

            Values1.append(conf)
            dct2 = dict(zip(Keys1, Values1))
            dict_2.append(dct2)
            Values1=[]


        
        #plt.savefig(r'E:\AI\detr_motive_ai\output_inference_'+str('detr_out')+'.png',dpi=400)

    run_worflow(im,model)
    i=i+1
    print(i)


Downloading: "https://github.com/facebookresearch/detr/archive/master.zip" to /root/.cache/torch/hub/master.zip
Downloading: "https://download.pytorch.org/models/resnet50-19c8e357.pth" to /root/.cache/torch/hub/checkpoints/resnet50-19c8e357.pth


  0%|          | 0.00/97.8M [00:00<?, ?B/s]

file_name:  00005388.jpg
image id:  0
annotation id: 0
image id:  0
annotation id: 1
image id:  0
annotation id: 2
image id:  0
annotation id: 3
image id:  0
annotation id: 4
1
file_name:  00000749.jpg
image id:  1
annotation id: 5
image id:  1
annotation id: 6
image id:  1
annotation id: 7
image id:  1
annotation id: 8
image id:  1
annotation id: 9
image id:  1
annotation id: 10
image id:  1
annotation id: 11
image id:  1
annotation id: 12
image id:  1
annotation id: 13
image id:  1
annotation id: 14
image id:  1
annotation id: 15
image id:  1
annotation id: 16
image id:  1
annotation id: 17
image id:  1
annotation id: 18
image id:  1
annotation id: 19
image id:  1
annotation id: 20
image id:  1
annotation id: 21
image id:  1
annotation id: 22
image id:  1
annotation id: 23
image id:  1
annotation id: 24
image id:  1
annotation id: 25
image id:  1
annotation id: 26
image id:  1
annotation id: 27
image id:  1
annotation id: 28
image id:  1
annotation id: 29
image id:  1
annotation id: 